# Get all the Gartenlaube Text in Wikisource

Mehr als 15.000 Artikel der Gartenlaube sind Ende 2021 in Wikisource erschlossen, ein vielfaches an Seiten der Illustrierten stehen hinter diesen Artikeln. 

## Frage 

Wie kommt man zum Texttranskript aller Gartenlaube-Artikel in Wikisource? (vgl. https://de.wikisource.org/wiki/Benutzer_Diskussion:Jeb#Gartenlaube_runterladen)

## Let's hack

Die MediaWiki-API bietet eine Vielzahl an Methoden um Daten aus MediaWikis - wie Wikisource - maschinell und im großen Stil zu extrahieren. Für große Projekte wie die Gartenlaube, die letztlich auch so sturkturiert sind wie sie strukturiert sind, geht es aber nicht ganz ohne Code. 

Was muss vorab beachtet werden?

* Der Text von Wikisource-Artikeln liegt nicht in den Seiten der strukturierten Zeitschriftenartikel, sondern in den Wiki-Artikel des `Seite:`-Namespaces
* Ein Wikisource-Großprojekt wie Die Gartenlaube ist nicht in einer einzigen Projektkategorie organisiert. Die einzelnen Seiten liegen in Jahrgangskategorien vor, die selbst eine Unterkategorie der Gartenlaube-Kategorie sind.
* Die MediaWiki-API bietet eine Extension an, um möglichst "Plain"-Text zu erhalten. Diese Extension `TextExctracts`(https://www.mediawiki.org/wiki/Extension:TextExtracts/de) ist aber für die Wikisource nicht verfügbar, da hier die Extension Proofread dies technisch gegenwärtig nicht ermöglicht. Daher ist ein Text-Output nur in einem gerenderte HTML oder im Wikitext möglich. Beide Varianten werden am Ende dieses Skripts im Output vereint.
* Mit der Python-Library `mwparserfromhell` wird noch zusätzlich ein plaintext ausgegeben, dieser Text basiert auf dem Wikicode, verliert aber sämtliche Textinhalte, die in Vorlagen gespeichert waren. Konkret sind dies Überschriften und Bildunterschriften. Dieser Volltext ist daher nur als Referenzwert zu verstehen und mit Vorsicht zu genießen.

### 1. Schritt - Alle Jahrgangskategorien parsen

In [1]:
import requests

S = requests.Session()

URL = "https://de.wikisource.org/w/api.php"

PARAMS = {
    "action": "query",
    "cmtitle": "Kategorie:Die Gartenlaube",
    "cmlimit":500,
    "cmtype": "subcat",
    "list": "categorymembers",
    "format": "json"
}

R = S.get(url=URL, params=PARAMS)
DATA = R.json()

Gartenlaube_SubCat = DATA["query"]["categorymembers"]

#for SubCat in Gartenlaube_SubCat:
#    print(SubCat["title"])

### 2. Für jede Subkategorie der Gartenlaube, Seiten des "Seite:"-Namespaces abrufen

In [2]:

pages = []
retDict = {}
for SubCat in Gartenlaube_SubCat:
    catPages = []
    PARAMS = {
    "action": "query",
    "gcmtitle": SubCat["title"],
    "gcmlimit": 500,
    "gcmnamespace":102,
    "generator": "categorymembers",
    "prop": "proofread|info",
    "format": "json"
    }

    R = S.get(url=URL, params=PARAMS)
    DATA = R.json()
    
    try:
        Gartenlaube_Seiten = DATA["query"]["pages"]
        #print(DATA)

        for Pages in Gartenlaube_Seiten:
            print(Gartenlaube_Seiten[Pages])
            pagedet = {}
            pagedet["pageid"] = Gartenlaube_Seiten[Pages]["pageid"]
            pagedet["title"] = Gartenlaube_Seiten[Pages]["title"]
            pagedet["proofread"] = Gartenlaube_Seiten[Pages]["proofread"]
            pagedet["lastrevid"] = Gartenlaube_Seiten[Pages]["lastrevid"]
            catPages.append(pagedet)

        try:
            PARAMS["gcmcontinue"] = DATA["continue"]["gcmcontinue"]
            R = S.get(url=URL, params=PARAMS)
            DATA = R.json()
            Gartenlaube_Seiten = DATA["query"]["pages"]
            for Pages in Gartenlaube_Seiten:
                pagedet = {}
                pagedet["pageid"] = Gartenlaube_Seiten[Pages]["pageid"]
                pagedet["title"] = Gartenlaube_Seiten[Pages]["title"]
                pagedet["proofread"] = Gartenlaube_Seiten[Pages]["proofread"]
                pagedet["lastrevid"] = Gartenlaube_Seiten[Pages]["lastrevid"]
                catPages.append(pagedet)
                #print(Pages["title"])
        except KeyError:
            pass

        
    except KeyError:
        pass
    
    retDict[SubCat["title"]]=catPages
pages.append(retDict)
print(pages)


{'pageid': 180682, 'ns': 102, 'title': 'Seite:Die Gartenlaube (1853) 001.jpg', 'proofread': {'quality': 4, 'quality_text': 'Fertig'}, 'contentmodel': 'proofread-page', 'pagelanguage': 'de', 'pagelanguagehtmlcode': 'de', 'pagelanguagedir': 'ltr', 'touched': '2021-05-05T18:45:41Z', 'lastrevid': 2964676, 'length': 3244}
{'pageid': 197740, 'ns': 102, 'title': 'Seite:Die Gartenlaube (1853) 002.jpg', 'proofread': {'quality': 4, 'quality_text': 'Fertig'}, 'contentmodel': 'proofread-page', 'pagelanguage': 'de', 'pagelanguagehtmlcode': 'de', 'pagelanguagedir': 'ltr', 'touched': '2021-05-05T18:46:41Z', 'lastrevid': 3272772, 'length': 4701}
{'pageid': 197741, 'ns': 102, 'title': 'Seite:Die Gartenlaube (1853) 003.jpg', 'proofread': {'quality': 4, 'quality_text': 'Fertig'}, 'contentmodel': 'proofread-page', 'pagelanguage': 'de', 'pagelanguagehtmlcode': 'de', 'pagelanguagedir': 'ltr', 'touched': '2021-05-05T18:46:41Z', 'lastrevid': 3272773, 'length': 6795}
{'pageid': 197742, 'ns': 102, 'title': 'Sei

{'pageid': 342712, 'ns': 102, 'title': 'Seite:Die Gartenlaube (1854) 001.jpg', 'proofread': {'quality': 4, 'quality_text': 'Fertig'}, 'contentmodel': 'proofread-page', 'pagelanguage': 'de', 'pagelanguagehtmlcode': 'de', 'pagelanguagedir': 'ltr', 'touched': '2021-05-05T18:50:21Z', 'lastrevid': 3631782, 'length': 3078}
{'pageid': 348254, 'ns': 102, 'title': 'Seite:Die Gartenlaube (1854) 002.jpg', 'proofread': {'quality': 4, 'quality_text': 'Fertig'}, 'contentmodel': 'proofread-page', 'pagelanguage': 'de', 'pagelanguagehtmlcode': 'de', 'pagelanguagedir': 'ltr', 'touched': '2021-05-05T18:50:26Z', 'lastrevid': 3273322, 'length': 8924}
{'pageid': 348256, 'ns': 102, 'title': 'Seite:Die Gartenlaube (1854) 003.jpg', 'proofread': {'quality': 4, 'quality_text': 'Fertig'}, 'contentmodel': 'proofread-page', 'pagelanguage': 'de', 'pagelanguagehtmlcode': 'de', 'pagelanguagedir': 'ltr', 'touched': '2021-05-05T18:50:26Z', 'lastrevid': 3273323, 'length': 8454}
{'pageid': 348073, 'ns': 102, 'title': 'Sei

{'pageid': 154239, 'ns': 102, 'title': 'Seite:Die Gartenlaube (1855) 001.jpg', 'proofread': {'quality': 4, 'quality_text': 'Fertig'}, 'contentmodel': 'proofread-page', 'pagelanguage': 'de', 'pagelanguagehtmlcode': 'de', 'pagelanguagedir': 'ltr', 'touched': '2021-05-05T18:44:27Z', 'lastrevid': 3534090, 'length': 5516}
{'pageid': 154240, 'ns': 102, 'title': 'Seite:Die Gartenlaube (1855) 002.jpg', 'proofread': {'quality': 4, 'quality_text': 'Fertig'}, 'contentmodel': 'proofread-page', 'pagelanguage': 'de', 'pagelanguagehtmlcode': 'de', 'pagelanguagedir': 'ltr', 'touched': '2021-05-05T18:44:27Z', 'lastrevid': 3534091, 'length': 8773}
{'pageid': 154241, 'ns': 102, 'title': 'Seite:Die Gartenlaube (1855) 003.jpg', 'proofread': {'quality': 4, 'quality_text': 'Fertig'}, 'contentmodel': 'proofread-page', 'pagelanguage': 'de', 'pagelanguagehtmlcode': 'de', 'pagelanguagedir': 'ltr', 'touched': '2021-05-05T18:44:27Z', 'lastrevid': 3534092, 'length': 8756}
{'pageid': 154242, 'ns': 102, 'title': 'Sei

{'pageid': 316126, 'ns': 102, 'title': 'Seite:Die Gartenlaube (1856) 001.jpg', 'proofread': {'quality': 4, 'quality_text': 'Fertig'}, 'contentmodel': 'proofread-page', 'pagelanguage': 'de', 'pagelanguagehtmlcode': 'de', 'pagelanguagedir': 'ltr', 'touched': '2021-05-05T18:49:49Z', 'lastrevid': 3744212, 'length': 5493}
{'pageid': 314328, 'ns': 102, 'title': 'Seite:Die Gartenlaube (1856) 002.jpg', 'proofread': {'quality': 4, 'quality_text': 'Fertig'}, 'contentmodel': 'proofread-page', 'pagelanguage': 'de', 'pagelanguagehtmlcode': 'de', 'pagelanguagedir': 'ltr', 'touched': '2021-05-05T18:49:47Z', 'lastrevid': 3128543, 'length': 8718}
{'pageid': 314330, 'ns': 102, 'title': 'Seite:Die Gartenlaube (1856) 003.jpg', 'proofread': {'quality': 4, 'quality_text': 'Fertig'}, 'contentmodel': 'proofread-page', 'pagelanguage': 'de', 'pagelanguagehtmlcode': 'de', 'pagelanguagedir': 'ltr', 'touched': '2021-05-05T18:49:47Z', 'lastrevid': 3744182, 'length': 8186}
{'pageid': 314331, 'ns': 102, 'title': 'Sei

{'pageid': 351541, 'ns': 102, 'title': 'Seite:Die Gartenlaube (1857) 001.jpg', 'proofread': {'quality': 4, 'quality_text': 'Fertig'}, 'contentmodel': 'proofread-page', 'pagelanguage': 'de', 'pagelanguagehtmlcode': 'de', 'pagelanguagedir': 'ltr', 'touched': '2021-05-05T18:50:32Z', 'lastrevid': 3732236, 'length': 5752}
{'pageid': 351174, 'ns': 102, 'title': 'Seite:Die Gartenlaube (1857) 002.jpg', 'proofread': {'quality': 4, 'quality_text': 'Fertig'}, 'contentmodel': 'proofread-page', 'pagelanguage': 'de', 'pagelanguagehtmlcode': 'de', 'pagelanguagedir': 'ltr', 'touched': '2021-05-05T18:50:31Z', 'lastrevid': 3422636, 'length': 8296}
{'pageid': 351098, 'ns': 102, 'title': 'Seite:Die Gartenlaube (1857) 003.jpg', 'proofread': {'quality': 4, 'quality_text': 'Fertig'}, 'contentmodel': 'proofread-page', 'pagelanguage': 'de', 'pagelanguagehtmlcode': 'de', 'pagelanguagedir': 'ltr', 'touched': '2021-05-05T18:50:30Z', 'lastrevid': 3535994, 'length': 8115}
{'pageid': 397109, 'ns': 102, 'title': 'Sei

...

{'pageid': 356353, 'ns': 102, 'title': 'Seite:Die Gartenlaube (1896) 0001.jpg', 'proofread': {'quality': 4, 'quality_text': 'Fertig'}, 'contentmodel': 'proofread-page', 'pagelanguage': 'de', 'pagelanguagehtmlcode': 'de', 'pagelanguagedir': 'ltr', 'touched': '2021-10-17T09:16:50Z', 'lastrevid': 3577849, 'length': 3508}
{'pageid': 356010, 'ns': 102, 'title': 'Seite:Die Gartenlaube (1896) 0002.jpg', 'proofread': {'quality': 4, 'quality_text': 'Fertig'}, 'contentmodel': 'proofread-page', 'pagelanguage': 'de', 'pagelanguagehtmlcode': 'de', 'pagelanguagedir': 'ltr', 'touched': '2021-08-20T16:54:31Z', 'lastrevid': 3824235, 'length': 9135}
{'pageid': 355969, 'ns': 102, 'title': 'Seite:Die Gartenlaube (1896) 0003.jpg', 'proofread': {'quality': 4, 'quality_text': 'Fertig'}, 'contentmodel': 'proofread-page', 'pagelanguage': 'de', 'pagelanguagehtmlcode': 'de', 'pagelanguagedir': 'ltr', 'touched': '2021-08-20T16:54:29Z', 'lastrevid': 3824234, 'length': 9382}
{'pageid': 310419, 'ns': 102, 'title': '

{'pageid': 142305, 'ns': 102, 'title': 'Seite:Die Gartenlaube (1897) 001.jpg', 'proofread': {'quality': 4, 'quality_text': 'Fertig'}, 'contentmodel': 'proofread-page', 'pagelanguage': 'de', 'pagelanguagehtmlcode': 'de', 'pagelanguagedir': 'ltr', 'touched': '2021-05-05T18:44:10Z', 'lastrevid': 3295981, 'length': 3776}
{'pageid': 142306, 'ns': 102, 'title': 'Seite:Die Gartenlaube (1897) 002.jpg', 'proofread': {'quality': 4, 'quality_text': 'Fertig'}, 'contentmodel': 'proofread-page', 'pagelanguage': 'de', 'pagelanguagehtmlcode': 'de', 'pagelanguagedir': 'ltr', 'touched': '2021-05-05T18:44:10Z', 'lastrevid': 2954895, 'length': 9291}
{'pageid': 142307, 'ns': 102, 'title': 'Seite:Die Gartenlaube (1897) 003.jpg', 'proofread': {'quality': 4, 'quality_text': 'Fertig'}, 'contentmodel': 'proofread-page', 'pagelanguage': 'de', 'pagelanguagehtmlcode': 'de', 'pagelanguagedir': 'ltr', 'touched': '2021-05-05T18:44:10Z', 'lastrevid': 2954896, 'length': 8925}
{'pageid': 142308, 'ns': 102, 'title': 'Sei

{'pageid': 356807, 'ns': 102, 'title': 'Seite:Die Gartenlaube (1898) 0000 b.jpg', 'proofread': {'quality': 4, 'quality_text': 'Fertig'}, 'contentmodel': 'proofread-page', 'pagelanguage': 'de', 'pagelanguagehtmlcode': 'de', 'pagelanguagedir': 'ltr', 'touched': '2021-05-05T18:50:43Z', 'lastrevid': 3628556, 'length': 11467}
{'pageid': 296416, 'ns': 102, 'title': 'Seite:Die Gartenlaube (1898) 0000 c.jpg', 'proofread': {'quality': 4, 'quality_text': 'Fertig'}, 'contentmodel': 'proofread-page', 'pagelanguage': 'de', 'pagelanguagehtmlcode': 'de', 'pagelanguagedir': 'ltr', 'touched': '2021-05-05T18:49:27Z', 'lastrevid': 3296076, 'length': 320}
{'pageid': 296417, 'ns': 102, 'title': 'Seite:Die Gartenlaube (1898) 0000 d.jpg', 'proofread': {'quality': 0, 'quality_text': 'Sofort fertig'}, 'contentmodel': 'proofread-page', 'pagelanguage': 'de', 'pagelanguagehtmlcode': 'de', 'pagelanguagedir': 'ltr', 'touched': '2021-05-05T18:49:27Z', 'lastrevid': 3296077, 'length': 220}
{'pageid': 296869, 'ns': 102

{'pageid': 348555, 'ns': 102, 'title': 'Seite:Die Gartenlaube (1899) 0000 a.jpg', 'proofread': {'quality': 4, 'quality_text': 'Fertig'}, 'contentmodel': 'proofread-page', 'pagelanguage': 'de', 'pagelanguagehtmlcode': 'de', 'pagelanguagedir': 'ltr', 'touched': '2021-05-05T18:50:27Z', 'lastrevid': 3665036, 'length': 469}
{'pageid': 357480, 'ns': 102, 'title': 'Seite:Die Gartenlaube (1899) 0000 b.jpg', 'proofread': {'quality': 4, 'quality_text': 'Fertig'}, 'contentmodel': 'proofread-page', 'pagelanguage': 'de', 'pagelanguagehtmlcode': 'de', 'pagelanguagedir': 'ltr', 'touched': '2021-05-05T18:50:45Z', 'lastrevid': 3501154, 'length': 10536}
{'pageid': 348521, 'ns': 102, 'title': 'Seite:Die Gartenlaube (1899) 0001.jpg', 'proofread': {'quality': 4, 'quality_text': 'Fertig'}, 'contentmodel': 'proofread-page', 'pagelanguage': 'de', 'pagelanguagehtmlcode': 'de', 'pagelanguagedir': 'ltr', 'touched': '2021-05-05T18:50:26Z', 'lastrevid': 3493218, 'length': 1074}
{'pageid': 357545, 'ns': 102, 'title

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



### 3. Für jede Seite die zugehörigen Text auslesen

* Für jeden Jahrgang wird ein JSON-File erzeugt nach dem Muster `GartenlaubeSeitenText_{Jahrgangskategorie}_{Timestamp}.json`und beinhaltet ein JSON-Objekt mit folgender Struktur:
```json
 [{"pageid" : {PAGEID},
   "title"   : {PAGETITLE},
   "html"    : {HTML_OUTPUT},
   "wikitext": {WIKI_MARKUP},
   "plaintxt": {mwparserfromhell(WIKI_MARKUP).strip_code)}
   }]
 ```

In [17]:
import mwparserfromhell
import time
import json

#print(pages[0]["Kategorie:Die Gartenlaube (1853)"])
#https://de.wikisource.org/w/api.php?action=parse&format=json&pageid=197745&prop=text%7Cwikitext

for page in pages[0]:
    SeitenText = []
    for wikisourcePage in pages[0][page]:
        print(wikisourcePage)
    
        PARAMS = {
        "action": "parse",
        "pageid": wikisourcePage["pageid"],
        "pageid": 197745,
        "prop":"text|wikitext",
        "format": "json"
        }
        R = S.get(url=URL, params=PARAMS)
        DATA = R.json()
        SeitenTextDet = {}
        SeitenTextDet["pageid"] = wikisourcePage["pageid"]
        SeitenTextDet["title"] = wikisourcePage["title"]
        SeitenTextDet["proofread"] = wikisourcePage["proofread"]
        SeitenTextDet["lastrevid"] = wikisourcePage["lastrevid"]
        SeitenTextDet["html"] = DATA["parse"]["text"]["*"]
        SeitenTextDet["wikitext"] = DATA["parse"]["wikitext"]["*"]
        wikicode = mwparserfromhell.parse(SeitenTextDet["wikitext"] )
        SeitenTextDet["plaintxt"] = wikicode.strip_code()
        SeitenText.append(SeitenTextDet)

    f = open("output/GartenlaubeSeitenText_"+page+"_"+str(time.time())[0:10]+".json", "w")
    print(json.dumps(SeitenText),file=f)
    f.close()      


IndexError: list index out of range

### 4. Merge der Jahrgangs-Files

* Die bestehenden Jahrgangs-Jsonfiles werden hier zu einer Gesamtdatei gemerged. 
* **Achtung**: Dieser Schritt läuft nur als python-Skript via Shell, nicht im Notebook.

In [ ]:
import glob
import time

read_files = glob.glob("/home/paws/Gartenlaube/output/*.json")
print(read_files)

with open("/home/paws/Gartenlaube/output/GartenlaubeSeiten_Text_"+str(time.time())[0:10]+".json", "wb") as outfile:
    outfile.write(b",".join([open(f, "rb").read() for f in read_files]))
